In [1]:
import quartz
from gnn import QGNN
import rl_dqn
import dgl
import torch
quartz_context = quartz.QuartzContext(gate_set=['h', 'cx', 'x', 't', 'tdg', 'ccz'], filename='../bfs_verified_simplified.json')
parser = quartz.PyQASMParser(context=quartz_context)
my_dag = parser.load_qasm(filename="barenco_tof_3_opt_path/subst_history_39.qasm")
init_graph = quartz.PyGraph(context=quartz_context, dag=my_dag)

Using backend: pytorch[22:17:11] /opt/dgl/src/runtime/tensordispatch.cc:43: TensorDispatcher: dlopen failed: 
/home/zikunli/anaconda3/envs/quantum/lib/python3.9/site-packages/dgl/tensoradapter/pytorch/libtensoradapter_pytorch_1.10.2.so: cannot open shared object file: No such file or directory


In [ ]:
# Pretraining using tof_3 circuit
# Preparaing data
from concurrent.futures import ProcessPoolExecutor

xfers_reward = [xfer.src_gate_count - xfer.dst_gate_count for xfer in quartz_context.get_xfers()]
xfers_reward = torch.tensor(xfers_reward, dtype=torch.float)
xfers_reward_mask = xfers_reward > 0

def get_dataset(i):
    dag_i = parser.load_qasm(filename="barenco_tof_3_opt_path/subst_history_" + str(i) + ".qasm")
    graph = quartz.PyGraph(context=quartz_context, dag=dag_i)
    dgl_graph = graph.to_dgl_graph()
    appliable_xfer_matrix = graph.get_available_xfers_matrix(context=quartz_context)
    appliable_xfer_matrix = torch.tensor(appliable_xfer_matrix, dtype=torch.float)
    # appliable_xfer_matrix = torch.tensor(appliable_xfer_matrix,dtype=torch.float)
    # appliable_xfer_matrix = torch.subtract(appliable_xfer_matrix, 1)
    # for i in range(appliable_xfer_matrix.shape[0]):
    #     pos_reward_mask = torch.logical_and(appliable_xfer_matrix[i] == 0, xfers_reward_mask)
    #     appliable_xfer_matrix[i][pos_reward_mask] = 1
    # appliable_xfer_matrix = torch.multiply(appliable_xfer_matrix, 2)
    # appliable_xfer_matrix = torch.subtract(appliable_xfer_matrix, 1)
    dgl_graph.ndata['label'] = appliable_xfer_matrix.clone().detach()
    return dgl_graph

idx_list = list(range(40))
with ProcessPoolExecutor(max_workers=32) as executor:
    results = executor.map(get_dataset, idx_list)

opt_path_dgls = [r for r in results]

In [ ]:
def weighted_mse_loss(input, target, weight):
    return (weight * (input - target) ** 2).mean()

def train_supervised(g, model, lr=0.01, epochs=20):
    optimizer = torch.optim.Adam(model.parameters(), lr=lr)
    all_logits = []
    best_val_acc = 0
    best_test_acc = 0

    features = g.ndata['gate_type']

    labels = g.ndata['label']
    train_mask = g.ndata['train_mask']
    val_mask = g.ndata['val_mask']
    test_mask = g.ndata['test_mask']
    num_pos = torch.sum((labels[train_mask] == 1).float())
    num_neg = torch.sum((labels[train_mask] == 0).float())

    weight = labels[train_mask]
    w_pos = torch.log(num_neg + 1) + 1
    w_neg = torch.log(num_pos + 1) + 1
    # w_pos = (num_neg + num_pos) / num_pos / 2
    # w_neg = (num_neg + num_pos) / num_neg / 2
    # w_pos_normalized, w_neg_normalized = w_pos/ (w_pos + w_neg), w_neg / (w_pos + w_neg)
    # print(w_pos_normalized, w_neg_normalized)
    weight[labels[train_mask] == 1] = w_pos
    weight[labels[train_mask] == 0] = w_neg
    print(w_pos, w_neg)
    # print(weight)

    losses = []
    for e in range(epochs):
        # Forward
        logits = model(g)

        # Compute loss
        # Note that we should only compute the losses of the nodes in the training set,
        # i.e. with train_mask 1.
        #print(logits)
        
        # loss = torch.nn.MSELoss()(logits[train_mask], labels[train_mask])
        loss = weighted_mse_loss(logits[train_mask], labels[train_mask], weight)
        losses.append(loss.item())
        # loss = torch.nn.CrossEntropyLoss()(logits[train_mask], labels[train_mask])
        pred = logits > 0.5

        # Compute accuracy on training/validation/test
        train_acc = (pred[train_mask] == labels[train_mask]).float().mean()
        val_acc = (pred[val_mask] == labels[val_mask]).float().mean()
        test_acc = (pred[test_mask] == labels[test_mask]).float().mean()

        train_recall = torch.sum((torch.logical_and((pred[train_mask] == 1), (labels[train_mask] == 1))).float()) / torch.sum((labels[train_mask] == 1).float())
        val_recall = torch.sum((torch.logical_and((pred[val_mask] == 1), (labels[val_mask] == 1))).float()) / torch.sum((labels[val_mask] == 1).float())
        test_recall = torch.sum((torch.logical_and((pred[test_mask] == 1), (labels[test_mask] == 1))).float()) / torch.sum((labels[test_mask] == 1).float())

        # Save the best validation accuracy and the corresponding test accuracy.
        if best_val_acc < val_acc:
            best_val_acc = val_acc
            best_test_acc = test_acc

        # Backward
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        all_logits.append(logits.detach())

        # TODO: print out false negative
        if e % 1 == 0:
            print('In epoch {}, loss: {:.5f}, train acc: {:.5f}, train recall: {:.5f}, val acc: {:.5f} (best {:.5f}), val recall: {:.5f}, test acc: {:.5f} (best {:.5f}), test recall: {:.5f}'.format(
                e, loss, train_acc, train_recall, val_acc, best_val_acc,val_recall, test_acc, best_test_acc, test_recall))
    
    return losses

def test(*, filename):
    test_dag = parser.load_qasm(filename=filename)
    test_graph = quartz.PyGraph(context=quartz_context, dag=test_dag)
    test_graph_dgl = test_graph.to_dgl_graph()
    appliable_xfer_matrix = test_graph.get_available_xfers_matrix(context=quartz_context)
    test_graph_dgl.ndata['label'] = torch.tensor(appliable_xfer_matrix,dtype=torch.float)
    labels = test_graph_dgl.ndata['label']

    with torch.no_grad():
        logits = model(test_graph_dgl)
        pred = logits > 0.5
        test_acc = (pred == labels).float().mean()
        print(f"test_acc: {test_acc:.6f}")

In [ ]:
# Pretraining
from random import sample
import matplotlib.pyplot as plt
import numpy as np

bg = dgl.batch(opt_path_dgls)
node_cnt = bg.num_nodes()
l = list(range(node_cnt))
train_rate = 0.7
val_rate = 0.15

train_num = int(node_cnt * train_rate)
val_num = int(node_cnt * val_rate)
test_num = node_cnt - train_num - val_num

train_sample = sample(l, train_num)
node_left = [n for n in l if n not in train_sample]
val_sample = sample(node_left, val_num)
test_sample = [n for n in node_left if n not in val_sample]

train_mask = [0] * node_cnt
val_mask = [0] * node_cnt
test_mask = [0] * node_cnt

for i in range(node_cnt):
    if i in train_sample:
        train_mask[i] = 1
    elif i in val_sample:
        val_mask[i] = 1
    elif i in test_sample:
        test_mask[i] = 1
    else:
        assert False

bg.ndata['train_mask'] = torch.tensor(train_mask,dtype=torch.bool) 
bg.ndata['val_mask'] = torch.tensor(val_mask,dtype=torch.bool) 
bg.ndata['test_mask'] = torch.tensor(test_mask,dtype=torch.bool) 

lr = 0.02
epoches = 40
model = QGNN(26, 128, quartz_context.num_xfers, 128)
losses = train_supervised(bg, model, lr=lr, epochs=epoches)

x = list(range(0, epoches))
fig, ax = plt.subplots()
ax.plot(x, losses)
ax.set(ylim=(0, 1))
plt.show()

In [2]:
# Get predicted reward
dag_39 = parser.load_qasm(filename="barenco_tof_3_opt_path/subst_history_39.qasm")
graph_39 = quartz.PyGraph(context=quartz_context, dag=dag_39)
dgl_graph_39 = graph_39.to_dgl_graph()

# with torch.no_grad():
#     logits = model(dgl_graph_39)

In [3]:
# Get predicted reward for certain action
all_nodes = graph_39.all_nodes()
i = 0
valid_xfer_dict = {}
for node in all_nodes:
    valid_xfer_dict[i] = graph_39.available_xfers(context=quartz_context, node=node)
    print(i, ": ", valid_xfer_dict[i])
    i += 1
# valid_xfer_dict

0 :  [3259, 3355]
1 :  [3337, 3461]
2 :  [3321, 3345, 3385]
3 :  [1725, 3337, 3461]
4 :  [3363]
5 :  [1907, 3337, 3461]
6 :  [368, 1351, 2098, 3321, 3345, 3385]
7 :  [398, 440, 441, 442, 444, 1091, 1172, 1231, 1232, 1233, 1235, 1471, 1472, 1473, 1475, 3337, 3461]
8 :  [3287, 3288, 3337, 3430, 3461, 3490]
9 :  [3363, 3583]
10 :  [3321, 3345, 3385]
11 :  [3224, 3337, 3360, 3461]
12 :  [3223, 3359]
13 :  [3241]
14 :  [3259, 3355]
15 :  [3337, 3461]
16 :  [3321, 3345, 3385]
17 :  [1725, 3337, 3461]
18 :  [3363]
19 :  [1907, 3337, 3461]
20 :  [368, 1351, 2098, 3321, 3345, 3385]
21 :  [398, 440, 441, 442, 444, 1091, 1172, 1231, 1232, 1233, 1235, 1471, 1472, 1473, 1475, 3337, 3461]
22 :  [3287, 3288, 3337, 3430, 3461, 3490]
23 :  []
24 :  [2613, 3321, 3345, 3385]
25 :  [3291, 3383]
26 :  [1205, 1477, 1817, 2105, 3224, 3337, 3360, 3461]
27 :  [1725, 3337, 3461]
28 :  [3223, 3359]
29 :  [3223, 3359]
30 :  [3363]
31 :  [3337, 3461]
32 :  [3321, 3345, 3385]
33 :  [1557, 1559, 1725, 3337, 3461]
34

In [4]:
# RL training
seq_lens, correct_cnts = rl_dqn.train(lr=5e-3, 
                        gamma=0.999, 
                        replay_times=20,
                        a_size=quartz_context.num_xfers, 
                        episodes=500, 
                        epsilon=0.5, 
                        train_epoch=10, 
                        max_seq_len=20, 
                        batch_size=10,
                        context=quartz_context, 
                        init_graph=init_graph, 
                        target_update_interval=5,
                        log_fn="RL.txt",
                        valid_xfer_dict=valid_xfer_dict)

  0%|          | 0/500 [00:00<?, ?it/s]

select node 28 and xfer 477
end
randomly select node 45 and xfer 3363
60
select node 28 and xfer 477
end
select node 28 and xfer 477
end
randomly select node 14 and xfer 3355
60
select node 18 and xfer 477
end
select node 28 and xfer 477
end
select node 28 and xfer 477
end
select node 28 and xfer 477
end
select node 28 and xfer 477
end
randomly select node 17 and xfer 1725
60
randomly select node 50 and xfer 1559
61
randomly select node 13 and xfer 3241
63
randomly select node 35 and xfer 3461
65
select node 38 and xfer 477
end
randomly select node 5 and xfer 1907
59
randomly select node 49 and xfer 1559
60
randomly select node 49 and xfer 928
61
randomly select node 29 and xfer 3223
61
select node 56 and xfer 477
end
select node 28 and xfer 477
end
randomly select node 2 and xfer 3321
60
randomly select node 7 and xfer 3461
62
select node 32 and xfer 477
end
select node 28 and xfer 477
end
randomly select node 36 and xfer 3326
58
select node 28 and xfer 477
end
randomly select node 19

  0%|          | 1/500 [00:13<1:49:46, 13.20s/it]

tensor([3399,  788, 3549,  788, 3549, 3549, 3549, 3549, 3549, 3549, 3549,  788,
        3549, 3549, 3549,  788, 3549,  788, 3549, 3549, 3549, 3549, 3549, 3549,
        3549, 3549,  788, 3549, 3549, 3549, 3549,  788, 3549, 3549, 3549, 3549,
        3549, 3549, 3549,  788, 3549, 3549, 3549, 3549, 3549, 3549,  788, 3549,
        3549, 3549, 3549, 3549, 3549, 3549,  788, 3549, 3549, 3549])
correct count is 0
end of episode 0
select node 28 and xfer 3549
end
randomly select node 52 and xfer 792 (unavailable)
end
randomly select node 43 and xfer 3355
60
randomly select node 18 and xfer 3363
62
randomly select node 27 and xfer 3291
64
randomly select node 43 and xfer 3363
66
select node 13 and xfer 3549
end
randomly select node 28 and xfer 3223
58
select node 12 and xfer 3549
end
select node 28 and xfer 3549
end
randomly select node 13 and xfer 3241
60
randomly select node 59 and xfer 2067 (unavailable)
end
randomly select node 47 and xfer 3385
60
select node 28 and xfer 3549
end
select node 

  0%|          | 2/500 [00:27<1:55:02, 13.86s/it]

...

tensor([3124, 1472, 3156, 1472, 3156, 1472, 3156, 1472, 3490, 3287, 3156, 3224,
        3223, 3223, 3156, 1472, 3156, 1472, 3156, 1472, 3156, 1472, 3490, 3156,
        3156, 3223, 3224, 1472, 3223, 3223, 3156, 1472, 3156, 1472, 3287, 1472,
        3326, 3156, 3156, 3156, 3155, 3156, 3156, 3156, 1472, 3156, 1472, 3156,
        1472, 3287, 1472, 3326, 3156, 3156, 3156, 3155, 3156, 3156])
correct count is 15
end of episode 455
select node 12 and xfer 3223
58
select node 27 and xfer 3223
58
randomly select node 44 and xfer 3363
60
randomly select node 3 and xfer 1725
62
select node 31 and xfer 3360
62
randomly select node 5 and xfer 3123
62
randomly select node 54 and xfer 440
62
select node 15 and xfer 3223
62
select node 31 and xfer 3360
62
randomly select node 12 and xfer 3321
64
select node 43 and xfer 3155
64
randomly select node 33 and xfer 3363
66
select node 32 and xfer 3223
66
select node 48 and xfer 3360
66
randomly select node 26 and xfer 3461
68
select node 27 and xfer 3223
68


 91%|█████████▏| 457/500 [5:47:42<44:55, 62.69s/it]

tensor([3124, 1472, 3156, 1472, 3156, 1472, 3156, 1472, 3490, 3287, 3287, 3224,
        3223, 3223, 3156, 1472, 3156, 1472, 3156, 1472, 3156, 1472, 3490, 3156,
        3287, 3223, 3224, 1472, 3223, 3223, 3156, 1472, 3156, 1472, 3287, 1472,
        3326, 3156, 3156, 3156, 3155, 3156, 3156, 3156, 1472, 3156, 1472, 3156,
        1472, 3287, 1472, 3326, 3156, 3156, 3156, 3155, 3156, 3156])
correct count is 15
end of episode 456
select node 12 and xfer 3223
58
randomly select node 5 and xfer 3461
60
randomly select node 10 and xfer 3490
60
randomly select node 23 and xfer 3337
62
select node 1 and xfer 3224
62
select node 24 and xfer 3223
62
select node 31 and xfer 3224
62
select node 44 and xfer 3155
62
randomly select node 60 and xfer 3438 (unavailable)
end
select node 12 and xfer 3223
58
randomly select node 57 and xfer 146 (unavailable)
end
randomly select node 44 and xfer 1725
60
select node 12 and xfer 3223
60
select node 30 and xfer 3360
60
randomly select node 7 and xfer 1235
61
sel

 91%|█████████▏| 457/500 [5:48:05<32:45, 45.70s/it]


KeyboardInterrupt: 

In [ ]:
import matplotlib.pyplot as plt

fig, ax = plt.subplots()
ax.plot(seq_lens)
plt.title("sequence length - training epochs")
plt.show()

In [ ]:
fig, ax = plt.subplots()
ax.plot(correct_cnts)
plt.title("correct counts - training epochs")
plt.show()

In [6]:
def find_56(fn):
    with open(fn, 'r') as f:
        for l in f:
            if l[:2] == 56:
                print("56 found!")
                return
    print("56 not found!")

find_56("RL.txt")

56 not found!
